# 使用嵌入进行文档搜索

## 概述
此示例演示如何使用 Gemini API 创建嵌入，以便您可以执行文档搜索。您将使用 Python 客户端库构建词嵌入，以便将搜索字符串或问题与文档内容进行比较。

在本教程中，您将使用嵌入对一组文档执行文档搜索，以询问与 Google Car 相关的问题。

## 前提条件
您可以在 Google Colab 中运行此快速入门。 

要在您自己的开发环境中完成本快速入门，请确保您的环境满足以下要求： 
- Python 3.9+ 
- 安装 jupyter 以运行笔记本

## 安装
首先，下载并安装 Gemini API Python 库。

In [1]:
!pip install -U -q google.generativeai

## !pip install -U -q google.colab

In [5]:
import textwrap
import numpy as np
import pandas as pd

import google.generativeai as genai
import google.ai.generativelanguage as glm

# # Used to securely store your API key
# from google.colab import userdata

from IPython.display import Markdown


### 获取 API 密钥
在使用 Gemini API 之前，您必须先获取 API 密钥。如果您还没有密钥，请在 Google AI Studio 中一键创建密钥。

在 Colab 中，将密钥添加到左侧面板“🔑”下的秘密管理器中。将其命名为 API_KEY。 获得 API 密钥后，将其传递给 SDK。您可以通过两种方式执行此操作：
- 将密钥放入 GOOGLE_API_KEY 环境变量中（SDK 将自动从那里获取它）。
- 将密钥传递给 genai.configure(api_key=...)

In [6]:
# Or use `os.getenv('API_KEY')` to fetch an environment variable.
# API_KEY=userdata.get('API_KEY')
GOOGLE_API_KEY = "YOUR-API-KEY"
genai.configure(api_key=GOOGLE_API_KEY)


```{tip}
要点：接下来，您将选择一个模型。任何嵌入模型都适用于本教程，但对于实际应用程序，选择特定模型并坚持使用非常重要。不同型号的输出互不兼容。
```
```{warning}
注意：目前，Gemini API [仅在某些区域可用](available_regions.md)。
```

In [7]:
for m in genai.list_models():
  if 'embedContent' in m.supported_generation_methods:
    print(m.name)


models/embedding-001


## 嵌入生成
在本节中，您将了解如何使用 Gemini API 中的嵌入为一段文本生成嵌入。

### 使用模型`embedding-001`对嵌入进行 API 更改
对于新的嵌入模型 embedding-001，有一个新的任务类型参数和可选标题（仅在 task_type=RETRIEVAL_DOCUMENT 时有效）。  
这些新参数仅适用于最新的嵌入模型。任务类型为：  

| 任务类型 | 描述 |
| --- | --- |
| RETRIEVAL_QUERY | 指定给定文本是搜索/检索设置中的查询。|
| RETRIEVAL_DOCUMENT | 指定给定文本是搜索/检索设置中的文档。|
| SEMANTIC_SIMILARITY | 指定给定文本将用于语义文本相似性 (STS)。|
| CLASSIFICATION | 指定嵌入将用于分类。|
| CLUSTERING | 指定嵌入将用于聚类。|

```{tip}
注意：指定 RETRIEVAL_DOCUMENT 的标题可为检索提供更高质量的嵌入。
```

In [8]:
title = "The next generation of AI for developers and Google Workspace"
sample_text = ("Title: The next generation of AI for developers and Google Workspace"
    "\n"
    "Full article:\n"
    "\n"
    "Gemini API & Google AI Studio: An approachable way to explore and prototype with generative AI applications")

model = 'models/embedding-001'
embedding = genai.embed_content(model=model,
                                content=sample_text,
                                task_type="retrieval_document",
                                title=title)

print(embedding)


{'embedding': [0.03411343, -0.05517662, -0.020209055, -0.0041249567, 0.058917783, 0.014129515, 0.0045353593, 0.0014303668, 0.05976634, 0.08292115, 0.007162964, 0.0069041685, -0.053083427, -0.010905125, 0.0321402, -0.037163995, 0.050372455, 0.019348344, -0.037328612, 0.026647927, 0.030781753, -0.011288501, -0.031485256, -0.060248993, -0.026219442, -0.009794235, 0.006630139, -0.01846516, -0.026324715, 0.020442624, -0.06317684, 0.014559574, -0.052296035, 0.016451128, -9.720217e-05, -0.051706687, -0.0054406044, -0.056967627, 0.011144145, -0.009201792, -0.0021951047, -0.1099701, -0.011712193, 0.021221714, 0.009171804, -0.029621972, 0.034534883, 0.039578073, 0.019021519, -0.06269169, 0.039473332, 0.052403256, 0.061814185, -0.034507945, -0.009557816, -0.0049551064, 0.017839009, -0.021176832, 0.015043588, 0.015390569, -0.006334281, 0.043696404, -0.028341983, 0.028433999, 0.01472686, -0.06585564, -0.044533554, 0.0055523133, 0.035775978, 0.031099156, 0.027357662, 0.028062241, 0.056972917, -0.054

## 构建嵌入数据库
以下是用于构建嵌入数据库的三个示例文本。您将使用 Gemini API 创建每个文档的嵌入。将它们转换为数据框以实现更好的可视化。

In [9]:
DOCUMENT1 = {
    "title": "Operating the Climate Control System",
    "content": "Your Googlecar has a climate control system that allows you to adjust the temperature and airflow in the car. To operate the climate control system, use the buttons and knobs located on the center console.  Temperature: The temperature knob controls the temperature inside the car. Turn the knob clockwise to increase the temperature or counterclockwise to decrease the temperature. Airflow: The airflow knob controls the amount of airflow inside the car. Turn the knob clockwise to increase the airflow or counterclockwise to decrease the airflow. Fan speed: The fan speed knob controls the speed of the fan. Turn the knob clockwise to increase the fan speed or counterclockwise to decrease the fan speed. Mode: The mode button allows you to select the desired mode. The available modes are: Auto: The car will automatically adjust the temperature and airflow to maintain a comfortable level. Cool: The car will blow cool air into the car. Heat: The car will blow warm air into the car. Defrost: The car will blow warm air onto the windshield to defrost it."}
DOCUMENT2 = {
    "title": "Touchscreen",
    "content": "Your Googlecar has a large touchscreen display that provides access to a variety of features, including navigation, entertainment, and climate control. To use the touchscreen display, simply touch the desired icon.  For example, you can touch the \"Navigation\" icon to get directions to your destination or touch the \"Music\" icon to play your favorite songs."}
DOCUMENT3 = {
    "title": "Shifting Gears",
    "content": "Your Googlecar has an automatic transmission. To shift gears, simply move the shift lever to the desired position.  Park: This position is used when you are parked. The wheels are locked and the car cannot move. Reverse: This position is used to back up. Neutral: This position is used when you are stopped at a light or in traffic. The car is not in gear and will not move unless you press the gas pedal. Drive: This position is used to drive forward. Low: This position is used for driving in snow or other slippery conditions."}

documents = [DOCUMENT1, DOCUMENT2, DOCUMENT3]

将字典的内容组织到数据框中以实现更好的可视化。

In [10]:
df = pd.DataFrame(documents)
df.columns = ['Title', 'Text']
df

Title  \
0  Operating the Climate Control System   
1                           Touchscreen   
2                        Shifting Gears   

                                                Text  
0  Your Googlecar has a climate control system th...  
1  Your Googlecar has a large touchscreen display...  
2  Your Googlecar has an automatic transmission. ...

获取每个文本正文的嵌入。将此信息添加到数据框中。

In [11]:
# Get the embeddings of each text and add to an embeddings column in the dataframe
def embed_fn(title, text):
  return genai.embed_content(model=model,
                             content=text,
                             task_type="retrieval_document",
                             title=title)["embedding"]

df['Embeddings'] = df.apply(lambda row: embed_fn(row['Title'], row['Text']), axis=1)
df


Title  \
0  Operating the Climate Control System   
1                           Touchscreen   
2                        Shifting Gears   

                                                Text  \
0  Your Googlecar has a climate control system th...   
1  Your Googlecar has a large touchscreen display...   
2  Your Googlecar has an automatic transmission. ...   

                                          Embeddings  
0  [-0.033361107, -0.021217084, -0.049581926, -0....  
1  [0.009660736, -0.030662702, -0.017281422, -0.0...  
2  [-0.04270796, -0.007160868, -0.03242516, -0.02...

## 文档搜索与问答
现在嵌入已经生成，让我们创建一个问答系统来搜索这些文档。您将询问有关超参数调整的问题，创建问题的嵌入，并将其与数据框中的嵌入集合进行比较。  

问题的嵌入将是一个向量（浮点值列表），它将使用点积与文档向量进行比较。从 API 返回的该向量已经标准化。点积表示两个向量之间方向的相似性。  

点积的值可以在 -1 和 1 之间（包含 -1 和 1）。如果两个向量之间的点积为 1，则这两个向量的方向相同。如果点积值为 0，则这些向量彼此正交或不相关。最后，如果点积为 -1，则向量指向相反方向并且彼此不相似。

请注意，使用新的嵌入模型 (`embedding-001`)，将任务类型指定为`QUERY`（用于用户查询）和`DOCUMENT`（嵌入文档文本时）。

| 任务类型 | 描述 |
| --- | --- |
| RETRIEVAL_QUERY | 指定给定文本是搜索/检索设置中的查询。|
| RETRIEVAL_DOCUMENT | 指定给定文本是搜索/检索设置中的文档。|



In [12]:
query = "How do you shift gears in the Google car?"
model = 'models/embedding-001'

request = genai.embed_content(model=model,
                              content=query,
                              task_type="retrieval_query")


使用`find_best_passage`函数计算点积，然后将数据帧按点积值从最大到最小进行排序，以从数据库中检索相关段落。

In [13]:
def find_best_passage(query, dataframe):
  """
  Compute the distances between the query and each document in the dataframe
  using the dot product.
  """
  query_embedding = genai.embed_content(model=model,
                                        content=query,
                                        task_type="retrieval_query")
  dot_products = np.dot(np.stack(dataframe['Embeddings']), query_embedding["embedding"])
  idx = np.argmax(dot_products)
  return dataframe.iloc[idx]['Text'] # Return text from index with max value


In [14]:
passage = find_best_passage(query, df)
passage


'Your Googlecar has an automatic transmission. To shift gears, simply move the shift lever to the desired position.  Park: This position is used when you are parked. The wheels are locked and the car cannot move. Reverse: This position is used to back up. Neutral: This position is used when you are stopped at a light or in traffic. The car is not in gear and will not move unless you press the gas pedal. Drive: This position is used to drive forward. Low: This position is used for driving in snow or other slippery conditions.'

## 问答应用
让尝试使用文本生成API来创建一个问答系统。在下面输入自己的自定义数据以创建简单的问题和回答示例。仍将使用点积作为相似性度量。

In [15]:
def make_prompt(query, relevant_passage):
  escaped = relevant_passage.replace("'", "").replace('"', "").replace("\n", " ")
  prompt = textwrap.dedent("""You are a helpful and informative bot that answers questions using text from the reference passage included below. \
  Be sure to respond in a complete sentence, being comprehensive, including all relevant background information. \
  However, you are talking to a non-technical audience, so be sure to break down complicated concepts and \
  strike a friendly and converstional tone. \
  If the passage is irrelevant to the answer, you may ignore it.
  QUESTION: '{query}'
  PASSAGE: '{relevant_passage}'

    ANSWER:
  """).format(query=query, relevant_passage=escaped)

  return prompt


In [16]:
prompt = make_prompt(query, passage)
print(prompt)

You are a helpful and informative bot that answers questions using text from the reference passage included below.   Be sure to respond in a complete sentence, being comprehensive, including all relevant background information.   However, you are talking to a non-technical audience, so be sure to break down complicated concepts and   strike a friendly and converstional tone.   If the passage is irrelevant to the answer, you may ignore it.
  QUESTION: 'How do you shift gears in the Google car?'
  PASSAGE: 'Your Googlecar has an automatic transmission. To shift gears, simply move the shift lever to the desired position.  Park: This position is used when you are parked. The wheels are locked and the car cannot move. Reverse: This position is used to back up. Neutral: This position is used when you are stopped at a light or in traffic. The car is not in gear and will not move unless you press the gas pedal. Drive: This position is used to drive forward. Low: This position is used for drivi

选择一种 Gemini 内容生成模型来找到您查询的答案。

In [17]:
for m in genai.list_models():
  if 'generateContent' in m.supported_generation_methods:
    print(m.name)

models/gemini-pro
models/gemini-pro-vision


In [19]:
# model = genai.GenerativeModel('gemini-ultra') 并没有gemini-ultra
model = genai.GenerativeModel('gemini-pro')
answer = model.generate_content(prompt)

In [20]:
Markdown(answer.text)

### 正常情况
## The provided passage does not contain information about how to shift gears in a Google car, so I cannot answer your question from this source.

The Google car has an automatic transmission, so you don't need to worry about shifting gears manually. Simply move the shift lever to the desired position, indicated on the gear shift, and the car will automatically shift to that gear.

## 下一步
要了解有关如何使用嵌入的更多信息，请查看可用的[示例](https://ai.google.dev/examples?keywords=embed)。  
要了解如何使用 Gemini API 中的其他服务，请访问[Python 快速入门](python_quickstart.ipynb)。